In [5]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import datetime as dt
from datetime import datetime
import folium
import folium.plugins as plugins
from sklearn.cluster import KMeans
import seaborn as sns; sns.set()
import geopy.distance
import math

In [3]:
# Show more rows when printing lists
pd.options.display.max_rows = 50

## Methods

### Load file

In [6]:
#get DateTime on the correct format (in accordance with excel file)
def load_file(file_name):
    df = pd.read_csv(file_name)
    
    # change date format
    df['DateTime'] = pd.TimedeltaIndex(df['DateTime'], unit='d') + dt.datetime(1899,12,30)
    
    # reformat coordinates to dot-separated floats
    df['Long'] = df['Long'].apply(lambda x: float(str(x).replace(',','.')))
    df['Lat'] = df['Lat'].apply(lambda x: float(str(x).replace(',','.')))
    
    # remove outliers
    #df = df[(df['Long'] <= 11) & (df['Long'] >= 10.62)]
    # only keep trip if it has a start and an end
    df = df[df.duplicated('Trip ID', keep=False)]
    return df

### Remove incomplete trips

In [7]:
def remove_incomplete_trips(df):
    df = df[df.duplicated('Trip ID', keep=False)]
    return df

### Get start and end data

In [8]:
def get_start_data(df):
    return df.loc[df['TripStage'] == 'Start']

def get_end_data(df):
    return df.loc[df['TripStage'] == 'End']

### Scatter plot

In [9]:
def plot_scatter(df, n, m):
    blue = 0
    red = 0
    # mark each station as a point
    for index, row in df.sample(n=n).iterrows():
        folium.CircleMarker([row['Lat'], row['Long']],
                            radius=3,
                            popup = "Type: " + str(row['TripStage']) + "\nTime: "+str(row['DateTime'])+"\nDuration: "+str(row['Trip duration (min)'])
                            +"\nTripID: "+str(row['Trip ID'])+"\nZone: "+str(row['Zone']),
                            fill = True,
                            color= "#3db7e4" if row['TripStage'] == "Start" else "#e43d43", # divvy color
                           ).add_to(m)
        if (row['TripStage'] == "Start"):
            blue += 1
        else:
            red += 1

    return m, blue, red

### Grid creator (returns polygons as geojson objects in a list)

In [10]:
#https://www.jpytr.com/post/analysinggeographicdatawithfolium/
def get_geojson_grid(upper_right, lower_left, lat_dim=8, lon_dim=15):
    """Returns a grid of geojson rectangles, and computes the exposure in each section of the grid based on the vessel data.

    Parameters
    ----------
    upper_right: array_like
        The upper right hand corner of "grid of grids" (the default is the upper right hand [lat, lon] of the USA).

    lower_left: array_like
        The lower left hand corner of "grid of grids"  (the default is the lower left hand [lat, lon] of the USA).

    n: integer
        The number of rows/columns in the (n,n) grid.

    Returns
    -------

    list
        List of "geojson style" dictionary objects   
    """

    all_boxes = []

    lat_steps = np.linspace(lower_left[0], upper_right[0], lat_dim+1)
    lon_steps = np.linspace(lower_left[1], upper_right[1], lon_dim+1)

    lat_stride = lat_steps[1] - lat_steps[0]
    lon_stride = lon_steps[1] - lon_steps[0]
    
    zone_counter = 1

    for lat in lat_steps[:-1]:
        for lon in lon_steps[:-1]:
           
            
            # Define dimensions of box in grid
            upper_left = [lon, lat + lat_stride]
            upper_right = [lon + lon_stride, lat + lat_stride]
            lower_right = [lon + lon_stride, lat]
            lower_left = [lon, lat]
                

            # Define json coordinates for polygon
            coordinates = [
                upper_left,
                upper_right,
                lower_right,
                lower_left,
                upper_left
            ]

            geo_json = {"type": "FeatureCollection",
                        "properties":{
                            "lower_left": lower_left,
                            "upper_right": upper_right,
                        },
                        "features":[],
                        "Number": zone_counter}


            grid_feature = {
                "type":"Feature",
                "geometry":{
                    "type":"Polygon",
                    "coordinates": [coordinates],
                }
            }

            geo_json["features"].append(grid_feature)

            all_boxes.append(geo_json)
            
            zone_counter+=1

    return all_boxes

### Plot n samples on the predefined grid

In [11]:
def plot_samples_on_grid(dataframe, n, excluded_zones):
    
    lower_left = [59.855331, 10.601628]
    upper_right = [59.973287, 10.950989]
    
    
    center = [lower_left[0]+(upper_right[0]-lower_left[0])/2,lower_left[1]+(upper_right[1]-lower_left[1])/2]

    #grid_size = int(np.sqrt(len(world.pNodes)))
    grid_size = (26,40)
    
    map = folium.Map(center, zoom_start = 10.8)
    

    grid = get_geojson_grid(lower_left, upper_right , lat_dim=grid_size[0], lon_dim=grid_size[1])
    
    count = 1
    for i, geo_json in enumerate(grid):
        if (str(len(grid)-i) not in excluded_zones):
            gj = folium.GeoJson(geo_json,
                    style_function=lambda feature: {#'fillColor': color,
                                                    'color':'#df80e8',
                                                    'weight': 2,
                                                    'dashArray': '5, 5',
                                                    'fillOpacity': 0.1}).add_to(map)
            popup_string = "Zone "+str(count)
            count += 1
            gj.add_child(folium.Popup(popup_string, max_width=400))

    map, start, end = plot_scatter(dataframe, n, map) 
    print("Start/End percentages: " + str((start/(start+end))*100) + "%/" + str((end/(start+end))*100)
            + "%")
    display(map)

### Take data as input, return the data that satisfies the time criteria

In [12]:
def hour_selector(data, hour_start, hour_end, include_weekends=False):
    if (hour_start == 0 and hour_end == 24):
        return data
    elif (hour_start > 24 or hour_start < 0 or hour_end > 24 or hour_end < 0):
        print("Invalid times")
        return
    elif (hour_start >= hour_end):
        print("Invalid times")
        return
    elif (hour_start != math.floor(hour_start)):
        print("Only whole hours permitted")
        return
    else:
        data_copy = data.copy()
        mask = (data_copy['DateTime'].dt.hour >= hour_start) & (data_copy['DateTime'].dt.hour <= (hour_end - 1))
        data_copy = data_copy.loc[mask]
        if ~include_weekends:
            mask = ((data_copy['DateTime'].dt.weekday != 5) & (data_copy['DateTime'].dt.weekday != 6))
            data_copy = data_copy.loc[mask]
        return data_copy
    
    
    

## Assign zone to each row, remove trips outside zones

In [17]:
file_name = "./data/2019_vy.csv"

list_zones = []
for zone in range(254):
    line = []
    line.append(zone+1)
    line.append(np.nan)
    line.append(np.nan)
    line.append(np.nan)
    list_zones.append(line)
    

zone_data = pd.DataFrame(list_zones, columns = ['Zone', 'Lower left', 'Upper Right', 'Center'])

#Size of zone area
lower_left = [59.855331, 10.601628]
upper_right = [59.973287, 10.950989]
center = [lower_left[0]+(upper_right[0]-lower_left[0])/2,lower_left[1]+(upper_right[1]-lower_left[1])/2]

data = load_file(file_name)
data_copy = data.copy()

#Start data and end data
start_data = get_start_data(data_copy)
end_data = get_end_data(data_copy)

excluded_zones = []

#List of polygons in grid
zones = get_geojson_grid(upper_right, lower_left, lat_dim=26, lon_dim=40)

# For each zone, mark all trips in that zone with the zone number
for zone in zones:
    upper_left = zone['features'][0]['geometry']['coordinates'][0][0]    
    upper_right = zone['features'][0]['geometry']['coordinates'][0][1]    
    lower_right = zone['features'][0]['geometry']['coordinates'][0][2]    
    lower_left = zone['features'][0]['geometry']['coordinates'][0][3]
    
    
    data_copy.loc[
        (data_copy.Long < float(upper_right[0]))
        & (data_copy.Long > float(upper_left[0]))
        & (data_copy.Lat > float(lower_left[1]))
        & (data_copy.Lat < float(upper_left[1])),'Zone'] = str(zone['Number']).strip()

    
    # Calculate new field "No. trips zone", which indicates how many starts and ends that have happened in that zone 
    data_copy.loc[
        data_copy.Zone == str(zone['Number']).strip(), 'No. trips zone'] = len(data_copy.loc[data_copy.Zone == str(zone['Number']).strip()])
    
    # add zones with less than x visits to excluded zones
    if (len(data_copy.loc[data_copy.Zone == str(zone['Number']).strip()]) <= 150):
        excluded_zones.append(str(zone['Number']).strip())

# Rename zone field in data to match that of the plot
counter = len(zones)-len(excluded_zones)
for zone in zones:
    if (str(zone['Number']) not in excluded_zones):
        data_copy.loc[data_copy.Zone == str(zone['Number']).strip(), 'Zone'] = counter
        
        zone_data.loc[(zone_data['Zone'] == str(counter)),'Lower Left'] = str(zone['properties']['lower_left'])
        zone_data.loc[(zone_data['Zone'] == str(counter)),'Upper Right'] = str(zone['properties']['upper_right'])
        
        
        counter -= 1
        
        
        
        
# remove starts and ends that happened outside of the included zones       
data_copy = data_copy[(~data_copy['Zone'].isin(excluded_zones)) & (~data_copy['Zone'].empty)]
        
# remove incomplete trips, so that the the system becomes "closed", 
# meaning that all starts and ends happen within the defined area
data_copy = remove_incomplete_trips(data_copy)
        

In [18]:
zone_data.head()

Zone  Lower left Upper Right  Center Lower Left
0     1         NaN         NaN     NaN        NaN
1     2         NaN         NaN     NaN        NaN
2     3         NaN         NaN     NaN        NaN
3     4         NaN         NaN     NaN        NaN
4     5         NaN         NaN     NaN        NaN

In [208]:
data_copy.head(500)

DateTime  Trip ID TripStage      Long       Lat  \
0   2018-12-31 11:39:21.888000000        1     Start  10.73382  59.92934   
1   2019-01-01 11:02:43.008000000        1       End  10.74900  59.91063   
2   2019-01-01 08:18:08.352000000        2     Start  10.73561  59.93056   
3   2019-01-01 08:42:50.976000000        2       End  10.80917  59.94132   
4   2019-01-01 14:34:39.360000000        3     Start  10.72983  59.92513   
..                            ...      ...       ...       ...       ...   
495 2019-01-06 07:53:24.000000000      248       End  10.79480  59.92132   
496 2019-01-06 07:58:05.664000000      249     Start  10.79480  59.92132   
497 2019-01-06 08:17:00.960000000      249       End  10.75874  59.91923   
498 2019-01-06 08:23:40.992000000      250     Start  10.75861  59.91907   
499 2019-01-06 08:45:05.759999999      250       End  10.75123  59.92289   

             Car ID  Trip duration (min) Zone  No. trips zone  
0    V5a15A3226E5F7          1403.350000  109          2482.0  
1    V5a15A3226E5F7          1403.350000  189          6666.0  
2    V5a15A3226E89D            24.716667  109          2482.0  
3    V5a15A3226E89D            24.716667   64           999.0  
4    V5a15A3226E999          1067.866667  129          3072.0  
..              ...                  ...  ...             ...  
495  V5a15A3226DEC4            37.533333  141          1015.0  
496  V5a15A3226DEC4            18.916667  141          1015.0  
497  V5a15A3226DEC4            18.916667  146          6889.0  
498  V5a15A3226DFD7            21.416667  146          6889.0  
499  V5a15A3226DFD7            21.416667  146          6889.0  

[500 rows x 9 columns]

In [12]:
print("Nr of excluded zones: " + str(len(excluded_zones)))
print("Nr of included zones: " + str(str(1040-len(excluded_zones))))

Nr of excluded zones: 786
Nr of included zones: 254


In [13]:
#nr of cars
print("Nr of cars in the system: " + str(data_copy['Car ID'].nunique()))

#Number of trips
count_new = len(data_copy.index)/2
count_old = len(data.index)/2
print("Number of trips in the system: " + str(count_new))
print("Number of trips in the original data: " + str(count_old))

Nr of cars in the system: 255
Number of trips in the system: 146198.0
Number of trips in the original data: 149405.0


## Plot scatter plot

In [18]:
lower_left = [59.855331, 10.601628]
upper_right = [59.973287, 10.950989]
center = [lower_left[0]+(upper_right[0]-lower_left[0])/2,lower_left[1]+(upper_right[1]-lower_left[1])/2]
map = folium.Map(center, zoom_start = 10.8)

plot_scatter(data_copy, 1000, map)

## Plot n samples on grid 

In [218]:
data_new = hour_selector(data_copy,2,5)

In [220]:
plot_samples_on_grid(data_new,2700, excluded_zones)

Start/End percentages: 48.92592592592593%/51.07407407407407%
